In [1]:
import pandas as pd
import seaborn as sns
import time
import re
import nltk
import math
import os
from Bio.SeqUtils.ProtParam import ProteinAnalysis
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

In [2]:
def fasta_parser(filename):
    if os.path.exists(filename):
        pass
    else:                     
        print("The file, %s, does not exist" % filename)
        
    file = open(filename,mode='r')
    rec_all = file.read()
    file.close()
    # remove all whitespace from string all_of_it
    rec_all = rec_all.replace(' ','')
    # split records by > 
    records = rec_all.split('>')
    # Parse out the headers & sequences for each record
    headers = []
    sequences = []
    for rec in records:
        s = ''
        data = rec.split('\n')
        sq = s.join(data[1:])
        if len(data[0]) > 0:
            headers.append(data[0])
   
        if (len(sq) > 0):
            sequences.append(s.join(data[1:]))
    
    return headers, sequences

In [3]:
# concatenate all relevant fasta files into one fasta file use glob
# see https://stackoverflow.com/questions/17749058/combine-multiple-text-files-into-one-text-file-using-python/17749339
# Note the code below works with no bizzare artifacts from globbing or concatenation
#read_files = glob.glob("*.fasta")

#with open("isomerase_2000.fasta", "wb") as outfile:
    #for f in read_files:
        #with open(f, "rb") as infile:
            #outfile.write(infile.read())

In [4]:
f_name = 'uniprot-oxidoreductase-reviewed.fasta'
t_head, t_seqs = fasta_parser(f_name)

In [5]:
for hd in t_head[0:5]:
    print(hd)
    print()

sp|Q8L540|LTO1_ARATHThiol-disulfideoxidoreductaseLTO1OS=ArabidopsisthalianaOX=3702GN=LTO1PE=1SV=1

sp|Q9AL95|NROR_CLOABNADH-rubredoxinoxidoreductaseOS=Clostridiumacetobutylicum(strainATCC824/DSM792/JCM1419/LMG5710/VKMB-1787)OX=272562GN=nroRPE=1SV=1

sp|P55931|ETFD_PIGElectrontransferflavoprotein-ubiquinoneoxidoreductase,mitochondrialOS=SusscrofaOX=9823GN=ETFDHPE=1SV=2

sp|Q16134|ETFD_HUMANElectrontransferflavoprotein-ubiquinoneoxidoreductase,mitochondrialOS=HomosapiensOX=9606GN=ETFDHPE=1SV=2

sp|Q9NZC7|WWOX_HUMANWWdomain-containingoxidoreductaseOS=HomosapiensOX=9606GN=WWOXPE=1SV=1



In [6]:
for sq in t_seqs[0:5]:
    print(sq)
    print()

MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKCSSSEPENGEDSAPSLSSSSSSSTSEVSTSNSSTYNWYTGIGGIGMLDTAYLTYLKVTGSDAFCPIGGGTCGDVLNSDYAVVFGVPLPVIGFVMYGVVTALSAELGEGNLPFGISKSNGRFALFGITTAMASASAYFLYILSTKLSGSSCLYCLVSAFLSFSLFFLSVKDVKLQEIQQVVGLQICLAIIVVASLTASYSTAQPIPSRSGDIELPYFRTEISSSSSPYAIALAKHLNSIGAKMYGAFWCSHCLEQKEMFGREAAKELNYVECFPDGYKKGTKILKACADAAIEGFPTWIINDKVLSGEIELAELAEMTGFSLDQANETNQLQ

MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLNEIIAKNKSIDDILIKKNDWYEKNNIKVITSEFATSIDPNNKLVTLKSGEKIKYEKLIIASGSIANKIKVPHADEIFSLYSYDDALKIKDECKNKGKAFIIGGGILGIELAQAIIDSGTPASIGIILEYPLERQLDRDGGLFLKDKLDRLGIKIYTNSNFEEMGDLIRSSCVITAVGVKPNLDFIKDTEIASKRGILVNDHMETSIKDIYACGDVAEFYGKNPGLINIANKQGEVAGLNACGEDASYSEIIPSPILKVSGISIISCGDIENNKPSKVFRSTQEDKYIVCMLKENKIDAAAVIGDVSLGTKLKKAIDSSKSFDNISSLDAILNNL

MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHYTIYPRDQDKRWEGVNMERFAEEADVVIVGAGPAGLSAATRLKQLAAQHEKDLRVCLVEKAAHIGAHTLSGACLDPRAFEELFPDWKEKGAPLNTPVTEDRFGILTEKYRIPVPILPGLPMNNHGNYVVRLGHLVSWMGEQAEALGVEVYPGYAAAEILFHEDGSVKGIATNDVGIQKDGAPKTTFERGLELHAKV

In [7]:
print(len(t_seqs))

46750


In [8]:
t_seqs2 = list(set(t_seqs))
print(len(t_seqs2))

39793


In [9]:
from Bio import SeqIO
records = list(SeqIO.parse(f_name, "fasta"))


In [10]:
seq_ids =[]
seqs = []
#for record in SeqIO.parse("isomerase_2000.fasta", "fasta"):
for record in SeqIO.parse(f_name, "fasta"):
    print(repr(record.seq))
    print()
    seq_ids.append(record.id)
    seqs.append(str(record.seq))

Seq('MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKCSSSEPENG...QLQ', SingleLetterAlphabet())

Seq('MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLNEIIAKNKS...NNL', SingleLetterAlphabet())

Seq('MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHYTIYPRDQD...NGM', SingleLetterAlphabet())

Seq('MLVPLAKLSCLAYQCFHALKIKKNYLPLCATRWSSTSTVPRITTHYTIYPRDKD...NGM', SingleLetterAlphabet())

Seq('MAALRYAGLDDTDSEDELPPGWEERTTKDGWVYYANHTEEKTQWEHPKTGKRKR...QSG', SingleLetterAlphabet())

Seq('MPSPQLLVLFGSQTGTAQDVSERLGREARRRRLGCRVQALDSYPVVNLINEPLV...TWA', SingleLetterAlphabet())

Seq('MGEKQRKLLVLYASQTGNALDAAERIGREAERRGLPASVVSTDEFDTSSLPHHE...AWS', SingleLetterAlphabet())

Seq('MSSSKKIVILYGSETGNAHDFATILSHRLHRWHFSHTFCSIGDYDPQDILKCRY...ETW', SingleLetterAlphabet())

Seq('MLVRLTKLSCPAYHWFHALKIKKCLPLCAPRCSSTSAVPQITTHYTVHPREKDK...NGM', SingleLetterAlphabet())

Seq('MILSAFSLEGKVAVVTGCDTGLGQGMALGLAQAGCDIVGINIVEPTETIEQVTA...LAR', SingleLetterAlphabet())

Seq('MQVDELLKPFPIKEFHPFPRALLGPGAHEMIGPEALKLGFKKTLVMTSGLRGSD...LLS', Si


Seq('MTTVLFVGLGLIGGSLASNIKYHNPNTNIIAYDADTSQLDKAKSIGIINEKCLN...YIQ', SingleLetterAlphabet())

Seq('MSQVSGTDVPDLGRRQFMNLLTFGTITGVAAGALYPIVKYFIPPSAGGTGGGVT...WWS', SingleLetterAlphabet())

Seq('MTQLSSNDVPSMGRRQFMNLLTFGTATGVALGALYPVANYFMPLRAGGGGGGTS...WWA', SingleLetterAlphabet())

Seq('MKITISGTGYVGLSNGLLIAQNHEVVALDILPSRVAMLNDRISPIVDKEIQQFL...GSD', SingleLetterAlphabet())

Seq('MNITFIGSGYVGLVSGIIMGYLGHNVTCLDNDEVKISKLNKQILPIYEAKLDEY...KAR', SingleLetterAlphabet())

Seq('MMLHIPGVLTKEQVAQCRDILDAADWADGNATSGAQSALAKRNRQLPEGSPAAR...ADA', SingleLetterAlphabet())

Seq('MATSSTSSTTSLCFPATSAAGARTSFRTTDTFLRYRRSRQLTRLKVRKAVVRSD...SLV', SingleLetterAlphabet())

Seq('MELLIHQLLSKEESKKITSNITKDNSCWIDGKTSAGSYAAKVKNNLQLKKDSEV...LGD', SingleLetterAlphabet())

Seq('MFEIKKICCIGAGYVGGPTCSVIAQMCPKIQVTVVDVNEARINAWNSDTLPIYE...PRV', SingleLetterAlphabet())

Seq('MKITTKVLIIGSGPAGLSAAIYTARSSLKPILINGMQPGGQLTMTTDVENYPGF...LNK', SingleLetterAlphabet())

Seq('MSTVLYRCPELLIGGEWRPGRHEQRLVVRNPATGEPLDELRLASADDLQLALQT...YVA', S

Seq('MSTHNEYDYIIIGAGSAGNVLATRLTEDADVSVLLLEAGGPDYRLDFRTQMPAA...KQD', SingleLetterAlphabet())

Seq('MFGKKNLKWLGVVATLMMTFVQLGGALVTKTGSADGCGSSWPLCHGALIPEFFP...DKQ', SingleLetterAlphabet())

Seq('MDQSMKPLLSPTERPRRHLTASVISFFLPNQFRLSTILCIGALLQTILCAVLPL...RDD', SingleLetterAlphabet())

Seq('MILLQNIKRCSLKQLKVLATLLLSLSLPTLEAAENRDSDSIVWHLDYQEALQKS...HQS', SingleLetterAlphabet())

Seq('MQQHYDYIIVGAGSAGCVLADRLSESGDHSVLLLEAGGSDKSIFIQMPTALSYP...PMR', SingleLetterAlphabet())

Seq('MEQNSAWFMEAKPVAIWLFLCSVMVILMVGIGGFTRLSKAGLSITEWKPITGTL...FPS', SingleLetterAlphabet())

Seq('MEYDYIIIGAGSAGNVLAARLTEDADVTVLLLEAGGPDYRLDFRTQMPAALAFP...SYP', SingleLetterAlphabet())

Seq('MSFQYPLLAPMTNSSVATNSNQPFLGQPWLVEERDACGVGFIANLRGKPDHTLV...TSV', SingleLetterAlphabet())

Seq('MKAQPKASHFIGGAFVEDKAGKPLPVIYPATGEEIASLYSATPGIIEAAYAAAL...SPY', SingleLetterAlphabet())

Seq('MRAQPKASHFIDGEYVEDAAGTVIESIYPATGEIIARLHAATPGIVEKAIAAAK...APY', SingleLetterAlphabet())

Seq('MGVIESPSSTTSGSAEEMAQAITGHEDSVLPVAIVGMGMRLPGGIHTPDELWGM...KAP', Si

Seq('MSADIVDIGHTGWMPSVQSLSILLVPGALVLVILYLCERQCNDLMGAPPPGPWG...VQD', SingleLetterAlphabet())

Seq('MLTKLLKISCTSRQCTFAKPYQAIPGPRGPFGMGNLYNYLPGIGSYSWLRLHQA...RRE', SingleLetterAlphabet())

Seq('MITETLLTICAAVFLCLSYRYAVGRPSGFPPGPPKIPLFGSYLFMLIINFKYLH...DRH', SingleLetterAlphabet())

Seq('MSAASSSSVLHLRTNQQLLSLRSLKNSTSVASQLAVTSGVSRRRSCTARCSVKK...ITN', SingleLetterAlphabet())

Seq('MTEKRERPGPLRWLRHLLDQLLVRILSLSLFRSRCDPPPLQRFPATELPPAVAA...RTE', SingleLetterAlphabet())

Seq('MDLIPNFAMETWVLVATSLVLLYIYGTHSHKLFKKLGIPGPTPLPFLGTILFYL...SGP', SingleLetterAlphabet())

Seq('MSNASDHVDVLIIGAGPAGLTTANSFNGSNCRVRLIDWKPAPLETGRADGLKSI...ANL', SingleLetterAlphabet())

Seq('MFTLVGLCLTIVHVAFAVVYFYLTWYHKYWDKRGVVTAEPLTILGSYPGILINK...LQK', SingleLetterAlphabet())

Seq('MDLLSALTLETWVLLAVILVLLYRLGTHRHGIFKKQGIPGPKPLPFLGTVLNYY...NGA', SingleLetterAlphabet())

Seq('MPDLIQTKSVVLGYGVKMVLAPAKAARSLLIREEAVWRFSLPRVLSTPTTMLET...ITV', SingleLetterAlphabet())

Seq('MACTLADSLLLFKGSYQKPVLRRDIAARYSPGIFSLNSNGLIQKRFRRQRNFVT...TCP', Si

Seq('MVKVGIIGGGGYTAGELIRLLINHPNVNIIFVHSYSNARNKIIDIHTGLIGEMD...NAF', SingleLetterAlphabet())

Seq('MKKIGIIGVSGYTGLELIKIILNHSGFKLSYLAATSEGEISEIFPQLAGVLNMK...YGI', SingleLetterAlphabet())

Seq('MVTISIIGGTGYTGSELLRILLNHPQVEIKHITSRKMDGVNITKVHPNLKNIKN...LKP', SingleLetterAlphabet())

Seq('MLKVAIVGASGYTGVELLRILHSHPEVAVTCVTSEQSAGRPVSSVFPSLRGRCD...VFP', SingleLetterAlphabet())

Seq('MKVAIVGASGYAGGELVRLLYHHSSAEVTCVTSRSLAGIPLSEVHPQLTGFSDL...LLP', SingleLetterAlphabet())

Seq('MIRAAIVGGTGYTGVELLRLLANHPNVEIVAITSRTEAGRPVSKLFPNLRGYLD...VIP', SingleLetterAlphabet())

Seq('MSKKIKVGIVGATGYTGVELLRLLAAHPDVEVAAVTSRSEAGTAVADYFPSLRG...LLP', SingleLetterAlphabet())

Seq('MAEISILGAGGLTGKELLLLLSRQKEHEVVHITSDKLAGKTLAEVFPEIPFPKN...LFP', SingleLetterAlphabet())

Seq('MAEKKKIGILGASGYTGAELVRLLLRHPRVEIVLLTADRRAGHKMGDVFPQFAP...LSS', SingleLetterAlphabet())

Seq('MQSTTFTRLLAAAALAATTLFAPATQAQGAQQYVNINPPMPSDTPGKIEVLEFF...SRK', SingleLetterAlphabet())

Seq('MNPLKAGDIAPKFSLPDQDGEQVNLTDFQGQRVLVYFYPKAMTPGCTVQACGLR...EHA', Si

...

Seq('MSQLLQQLGTDNEFIRRHNGPASSEHQHMLNTIGAETLQQLIEETVPSSIRLPQ...YEE', SingleLetterAlphabet())

Seq('MAGSSLRQVAVFGATGSIGASALDVIARHPERLRASLLSAGSKVDELLALCATH...LHA', SingleLetterAlphabet())

Seq('MIIKPRVRGFICVTTHPVGCEANVKEQIDYVTSHGPIANGPKKVLVIGASTGYG...TTV', SingleLetterAlphabet())

Seq('MGFLQGKKILITGMISERSIAYGIAKACREQGAELAFTYVVDKLEERVRKMAAE...TEG', SingleLetterAlphabet())

Seq('MKLEHPDRLMNRTPLSLAALETHDAFAERHIGPDAASQQAMLDTLGFATRAALI...DYA', SingleLetterAlphabet())

Seq('MTKQTLTQLEQHDLFLRRHIGPDSSQQQEMLNYVGAESLDDLTAQIVPESIRLS...DYE', SingleLetterAlphabet())

Seq('MKLEHPDRLMNRTPLSLAALETHDAFAERHIGPDAASQQAMLDTLGFASRAALI...DYA', SingleLetterAlphabet())

Seq('MSDHSTFADRHIGLDSQAVATMLAVIGVDSLDDLAVKAVPAGILDTLTDTGAAP...AFA', SingleLetterAlphabet())

Seq('MIAVRHLTILGSTGSIGVSTLDVVARHPDRFRVVALTANKSVQKILEQCRRFEP...CLA', SingleLetterAlphabet())

Seq('MSWHQAVWNEPLIFEYKGKGRIGFKIPEEEELKKEISINIPEKLRRKEIDLPEL...SLK', SingleLetterAlphabet())

Seq('MTQNLSQLEHNDAFIQRHIGSSVEQQQQMLAAVGASSLSTLIQQIVPADIQLPG...DYE', Si

Seq('MIIYLISLLPIIVATLMLYQRWWRSNIPPGPKPKFLLGNLHQMKPLWTHSFSEW...PLD', SingleLetterAlphabet())

Seq('MKAVIFAYHDMGCQGVQAVLDAGYEIAAIFTHADNPAENTFFGSVSRQAAELGI...RAS', SingleLetterAlphabet())

Seq('MLDIKGYLVLFFLWFISTILIRSIFKKPQRLRLPPGPPISIPLLGHAPYLRSLL...FAA', SingleLetterAlphabet())

Seq('MKAVIFAYHDMGCQGVQAVLDAGYEIAAIFTHADNPAENTFFGSVSRLAAGLGI...RAS', SingleLetterAlphabet())

Seq('MESRKGIKEVSMNFLDQLDAIIQNKHMLEHPFYMKWSKGELTKEQLQAYAKDYY...HKA', SingleLetterAlphabet())

Seq('MDFNLNDEQELFVAGIRELMASENWEAYFAECDRDSVYPERFVKALADMGIDSL...QYR', SingleLetterAlphabet())

Seq('MVVKKIALFGATGNTGLTTLAQAVQAGYEVTVLVRDPSRLPSEGPQPAHVVVGD...VYE', SingleLetterAlphabet())

Seq('MSLINKEILPFTAQAFDPKKDQFKEVTQEDLKGSWSVVCFYPADFSFVCPTELE...GKI', SingleLetterAlphabet())

Seq('MTVRDWANRGQTYVNARAPNLLGRFRSTDDEDENNPSTELATDTTSAYGSTAAS...IAN', SingleLetterAlphabet())

Seq('MKLAVYGKGGIGKSTTSCNISIALAKRGKKVLQIGCDPKSDSTFTLTGFLIPTI...DLV', SingleLetterAlphabet())

Seq('MSSELVKRHGHTHYANIPYGYYVLIVSFFYLVFLGVLRIILKPRAAGFNSSKRS...YAL', Si

Seq('MTKQTLTELEQHELFLTRHIGPDADEQQAMLNYVGAESLEDLTAQIVPESIRLG...DYE', SingleLetterAlphabet())

Seq('MSDHSTFADRHIGLDSQAVATMLAVIGVDSLDDLAVKAVPAGILDTLTDTGAAP...AFA', SingleLetterAlphabet())

Seq('MIIKPRVRGFICVTTHPVGCEANVKEQIDYVTSHGPIANGPKKVLVIGASTGYG...TTA', SingleLetterAlphabet())

Seq('MQNMVILGATGSIGASTLSVISANPTAYRVYALVANASVDKMLTLCLAHRPQVA...KFA', SingleLetterAlphabet())

Seq('MTQTLSQLENSGAFIERHIGPDAAQQQEMLNAVGAQSLNALTGQIVPKDIQLAT...EYQ', SingleLetterAlphabet())

Seq('MVVLGSTGSIGVNTLEIARRYDIEIEGLVAGNNYEVLNAQIKEFKPKYVVVKDL...NFV', SingleLetterAlphabet())

Seq('MGATALRKVSIFGATGSIGQNTIDLIARDPDAYDVVALSGGANIAQLAADARRL...RAG', SingleLetterAlphabet())

Seq('MPLNLPLSALEQHDEFIGRHIGPCSTEMATMLTAIGADSLEQLIDQTVPAAIRL...YAD', SingleLetterAlphabet())

Seq('MPVSRSPIEDLANGFARRHIGPSPQEIAAMLRAVGAPSLDALMGETLPAAIRQA...AAE', SingleLetterAlphabet())

Seq('MFLQNKNVVVMGVANKKSIAWGCAKALKDQGANVIYTYQNERMKKQVVKLADEN...HLT', SingleLetterAlphabet())

Seq('MTRTSPTLPVIILGAGMVGLTLAQALKKAGIPYEVYERDSAADTEKGRGWALTV...IAV', Si

Seq('MTQTLSQLENRGAFIERHIGPDAAQQQEMLNAVGAESLNALTGQIVPKDIQLAT...DYQ', SingleLetterAlphabet())

Seq('MSDHSTFADRHIGLDSQAVATMLAVIGVDSLDDLAVKAVPAGILDTLTDTGAAP...AFA', SingleLetterAlphabet())

Seq('MQYLTILGSTGSIGRSTLDIVRRHPDRFAVTALTANQGVAQMMSDCLEFHPSYA...LAV', SingleLetterAlphabet())

Seq('MTAHRTPLSELEQAMPFEQRHIGPDHEARAKMLAQVGYGSLDELTAAAVPDVIK...YED', SingleLetterAlphabet())

Seq('MTQTLSQLENSGAFIERHIGPDAAQQQEMLNAVGAQSLNALTGQIVPKDIQLAT...EYQ', SingleLetterAlphabet())

Seq('MSGSSLRRVAVFGATGSIGASALDVIARHPERLRASVLSAGSKVDALLALCVLH...LHA', SingleLetterAlphabet())

Seq('MKKISVLGSTGSIGKKTVDLLLKRKEEYQVEALSTCSNFALLACQAKLLNARYV...AYS', SingleLetterAlphabet())

Seq('MTQTLSQLENSGAFIERHIGPDAAQQQEMLNAVGAQSLNALTGQIVPKDIQLAT...EYQ', SingleLetterAlphabet())

Seq('MQQEEIIEGYYGASKGLKKSGIYAKLDFLQSATGLILALFMIAHMFLVSSILIS...HKE', SingleLetterAlphabet())

Seq('MTHPIIHDLENRYTSKKYDPSKKVSQEDLAVLLEALRLSASSINSQPWKFIVIE...TIL', SingleLetterAlphabet())

Seq('MTLSIIVAHDKQRVIGYQNQLPWHLPNDLKHVKQLTTGNTLVMGRKTFNSIGKP...KGK', Si

Seq('MSWGRLSRLLKPALLCGALAVPGLAGTMCASRDDWRCARSMHEFAAKDIDGHMV...CYL', SingleLetterAlphabet())

Seq('MTLSNQLSDLRLFRQYAYIDGKWTHGDAGREEAVFDPATGEAIGHIPVLEVEQI...SGS', SingleLetterAlphabet())

Seq('MKMMNGEDATDQMIKESFFITHGNPILTVEDTHPLRPFFETWREKIFSKKPKAI...TSA', SingleLetterAlphabet())

Seq('MLRECDYSQALLEQVNQAISDKTPLVIQGSNSKAFLGRPVTGQTLDVRCHRGIV...AEL', SingleLetterAlphabet())

Seq('MKAIVVKPPKPGVEVRDLSQVIRHGSGTVKVRILENGICGSDREIVKGELTTAR...KWS', SingleLetterAlphabet())

Seq('MSQNSNPAVVLEKVGDIAIEQRPIPTIKDPHYVKLAIKATGICGSDIHYYRSGG...GPE', SingleLetterAlphabet())

Seq('MDRIIQSPGKYIQGADVINRLGEYLKPLAERWLVVGDKFVLGFAQSTVEKSFKD...EWE', SingleLetterAlphabet())

Seq('MSILYEERLDGALPDVDRTSVLMALREHVPGLEILHTDEEIIPYECDGLSAYRT...ERF', SingleLetterAlphabet())

Seq('MVTEQEVEAIGKTLVDSTQPLQARFRALFTLRGLGGPDAISWISRGFEDSSALL...PPP', SingleLetterAlphabet())

Seq('MEFSFSSPALYIVYFLLFFVVRQLLKPKSKKKLPPGPRTLPLIGNLHQLSGPLP...VND', SingleLetterAlphabet())

Seq('MGFSPSSSWFLHPQLHHVVSKMSYFDAFLFYIVHLVDKLGLWHRFPVLLGVAYL...SAP', Si

In [11]:
print(len(seq_ids))
print()
print(len(seqs))

46750

46750


In [12]:
seqs[0:3]

['MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKCSSSEPENGEDSAPSLSSSSSSSTSEVSTSNSSTYNWYTGIGGIGMLDTAYLTYLKVTGSDAFCPIGGGTCGDVLNSDYAVVFGVPLPVIGFVMYGVVTALSAELGEGNLPFGISKSNGRFALFGITTAMASASAYFLYILSTKLSGSSCLYCLVSAFLSFSLFFLSVKDVKLQEIQQVVGLQICLAIIVVASLTASYSTAQPIPSRSGDIELPYFRTEISSSSSPYAIALAKHLNSIGAKMYGAFWCSHCLEQKEMFGREAAKELNYVECFPDGYKKGTKILKACADAAIEGFPTWIINDKVLSGEIELAELAEMTGFSLDQANETNQLQ',
 'MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLNEIIAKNKSIDDILIKKNDWYEKNNIKVITSEFATSIDPNNKLVTLKSGEKIKYEKLIIASGSIANKIKVPHADEIFSLYSYDDALKIKDECKNKGKAFIIGGGILGIELAQAIIDSGTPASIGIILEYPLERQLDRDGGLFLKDKLDRLGIKIYTNSNFEEMGDLIRSSCVITAVGVKPNLDFIKDTEIASKRGILVNDHMETSIKDIYACGDVAEFYGKNPGLINIANKQGEVAGLNACGEDASYSEIIPSPILKVSGISIISCGDIENNKPSKVFRSTQEDKYIVCMLKENKIDAAAVIGDVSLGTKLKKAIDSSKSFDNISSLDAILNNL',
 'MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHYTIYPRDQDKRWEGVNMERFAEEADVVIVGAGPAGLSAATRLKQLAAQHEKDLRVCLVEKAAHIGAHTLSGACLDPRAFEELFPDWKEKGAPLNTPVTEDRFGILTEKYRIPVPILPGLPMNNHGNYVVRLGHLVSWMGEQAEALGVEVYPGYAAAEILFHEDGSVKGIATNDVGIQKDGAPKTTFER

In [13]:
seqID = []
for item in records:
    seqID.append(item.id)
    print(item.id)
    print()

sp|Q8L540|LTO1_ARATH

sp|Q9AL95|NROR_CLOAB

sp|P55931|ETFD_PIG

sp|Q16134|ETFD_HUMAN

sp|Q9NZC7|WWOX_HUMAN

sp|Q9UHB4|NDOR1_HUMAN

sp|Q6NPS8|NDOR1_ARATH

sp|Q12181|NDOR1_YEAST

sp|Q921G7|ETFD_MOUSE

sp|P37769|KDUD_ECOLI

sp|Q9RCG0|MNO_AMYME

sp|O22854|ETFQO_ARATH

sp|Q8J2V8|P2OX_TRIMT

sp|Q9T0A4|NDHS_ARATH

sp|Q6QWR1|P2OX_PHACH

sp|Q6UG02|P2OX_PHLGI

sp|Q6UPE1|ETFD_RAT

sp|Q9LVM2|NDHN_ARATH

sp|Q8PZ67|FPOF_METMA

sp|Q9CAC5|NDHL_ARATH

sp|P77526|YFCG_ECOLI

sp|Q8U3K2|GAPOR_PYRFU

sp|P72579|OFOB_SULSP

sp|P72578|OFOA_SULSP

sp|Q91WL8|WWOX_MOUSE

sp|P15559|NQO1_HUMAN

sp|Q8YW84|NDHM_NOSS1

sp|Q8DKZ3|NDHL_THEEB

sp|Q8YQS7|PSBA3_NOSS1

sp|A6QJ00|MTLD_STAAE

sp|Q033G3|MTLD_LACLS

sp|B5LMP9|PSBB_CICAR

sp|A0T0G9|PSBA_PHATC

sp|A2BP21|PSBA_PROMS

sp|Q09MG2|PSBF_CITSI

sp|Q08CS6|MOXD2_DANRE

sp|A4QK44|PSBB_ARAHI

sp|Q81MI9|MTND_BACAN

sp|P41644|PSBD_PINTH

sp|Q8RSW3|PSBE_SYNP2

sp|B5LMM1|PSBD_CICAR

sp|Q06GW8|PSBH_DRIGR

sp|Q31ZB5|MTOX_SHIBS

sp|P69384|PSBE_TOBAC

sp|Q7HIV0|PSBF_HYDCA

sp|B2J6T

sp|C4ZR74|ULAE_ECOBW

sp|B1XDU8|ULAE_ECODH

sp|O49312|YUC7_ARATH

sp|Q8Y5F1|Y2113_LISMO

sp|O32175|YUSI_BACSU

sp|O05616|VANA_PSEUH

sp|O28082|Y2201_ARCFU

sp|A7GVD5|Y3909_BACCN

sp|O26799|VORC_METTH

sp|P0C1E8|Y2355_CORGL

sp|P0A3X4|Y2533_BORPA

sp|P9WJJ0|Y1812_MYCTO

sp|P9WJJ1|Y1812_MYCTU

sp|A0A443HK11|VDTE1_BYSSP

sp|Q02873|YP107_YEAST

sp|Q9F723|Y301_CHLTE

sp|Q9LIG0|Y3136_ARATH

sp|Q9HZ00|Y3240_PSEAE

sp|B7LNV2|SSUD_ESCF3

sp|Q2YS77|Y537_STAAB

sp|A6UU98|WECC_META3

sp|Q6GBP9|Y546_STAAS

sp|Q72X61|Y5517_BACC1

sp|P23171|YRUB_CLOPA

sp|O89049|TRXR1_RAT

sp|P43496|TRXB_PENCH

sp|Q56632|VIBA_VIBCH

sp|P0CR36|TSC10_CRYNJ

sp|A7WZ30|Y585_STAA1

sp|Q7AKN0|WHIB_STRCO

sp|Q7AKI9|WHID_STRCO

sp|Q05016|YM71_YEAST

sp|Q68WY1|Y384_RICTY

sp|Q03102|YMN1_YEAST

sp|Q10RE2|YUC8_ORYSJ

sp|G2QDQ9|VAO15_MYCTT

sp|O34295|TTUC5_AGRVI

sp|Q46799|XDHA_ECOLI

sp|P80907|VORA_METTM

sp|O31820|YNEN_BACSU

sp|P53878|YNS1_YEAST

sp|P9WMV4|Y1279_MYCTO

sp|Q2JRM5|Y2611_SYNJA

sp|Q6GDV6|Y2567_STAAR

sp|P9WJP8|Y

sp|Q89KD9|CTAA_BRADU

sp|A0A0C6DUU3|BET2_PLEBE

sp|A9VUA7|CTAA_BACMK

sp|B7GYG5|BETA_ACIB3

sp|A7Z4B0|CTAA_BACVZ

sp|Q8YGI7|CTAA_BRUME

sp|A0A0C6DWS6|BET3_PLEBE

sp|A1USH8|CTAA_BARBK

sp|A9IVC8|CTAA_BART1

sp|Q1QXE1|BETA1_CHRSD

sp|A9MAG4|CTAA_BRUC2

sp|B0V945|BETA_ACIBY

sp|C0RIC2|CTAA_BRUMB

sp|Q6FDF9|BETA_ACIAD

sp|P94346|CTAA_GEOTD

sp|P0AA88|DSBE_SHIFL

sp|A4ILW9|CTAA_GEOTN

sp|B8H551|CTAA_CAUVN

sp|Q1BQE2|BETA_BURCA

sp|Q11J69|CTAA_CHESB

sp|C4L5D6|CTAA_EXISA

sp|A4JJG6|BETA_BURVG

sp|Q9PAN4|DSBE_XYLFA

sp|A8AJN0|BETA_CITK8

sp|B0UR12|CTAA_METS4

sp|Q2GCS4|CTAA_NEOSM

sp|B1XE52|BETA_ECODH

sp|B7KV80|CTAA_METC4

sp|A7ZWV4|BETA_ECOHS

sp|A9W350|CTAA_METEP

sp|B7MCD0|BETA_ECO45

sp|Q0TKW1|BETA_ECOL5

sp|B2TCJ8|BETA_PARPJ

sp|B3CRU7|CTAA_ORITI

sp|Q02DZ0|BETA_PSEAB

sp|A6X2G7|BETA_OCHA4

sp|A7HXA1|CTAA_PARL1

sp|Q6D6D9|BETA_PECAS

sp|B0KN19|BETA_PSEPG

sp|Q2K9W9|CTAA_RHIEC

sp|B4EX94|BETA_PROMH

sp|Q4ZM63|BETA_PSEU2

sp|C3PMV5|CTAA_RICAE

sp|B5ZUG2|BETA_RHILW

sp|A1VZK8|DSBI_CAMJJ

s


sp|B0CLB5|ARGC_BRUSI

sp|C4ZZA2|ASTD_ECOBW

sp|B1WYI6|ARGC_CROS5

sp|Q5P7T9|ARGC_AROAE

sp|D3J0Z1|CHADH_ASPFM

sp|Q41931|ACCO2_ARATH

sp|Q94A78|ACCH4_ARATH

sp|Q5AUZ6|ATNA_EMENI

sp|P55544|CPXP_SINFN

sp|P31718|CPXX_RHORH

sp|P31237|ACCO_ACTDE

sp|P24467|CPXD_RHIRD

sp|Q1B0P7|ACDH2_MYCSS

sp|Q0S005|ACDH5_RHOJR

sp|Q5AUZ9|ATNE_EMENI

sp|C1AYB3|ACDH5_RHOOB

sp|Q6I681|ACET1_MAIZE

sp|P37845|CHLB_EQUAR

sp|Q85FG5|CHLL_ADICA

sp|A9BEG6|CHLL_PROM4

sp|Q85X76|CHLB_PINKO

sp|A2CDU0|ACSF_PROM3

sp|C3NEV8|G3P_SULIY

sp|O34591|ACOB_BACSU

sp|P34731|FAS1_CANAX

sp|Q2UB88|3HAO2_ASPOR

sp|B1HRX9|FOLD_LYSSC

sp|Q2HD63|3HAO_CHAGB

sp|Q89187|3BHS_VAR67

sp|Q5JHB5|G3P_THEKO

sp|Q83V26|3HAO_PSEFL

sp|Q28SE8|3HAO_JANSC

sp|Q6CKK7|ACOX_KLULA

sp|P26439|3BHS2_HUMAN

sp|A2VCW9|AASS_RAT

sp|P05335|ACOX4_CANMA

sp|Q8NLB6|3HBH_CORGL

sp|Q67477|3BHS_FOWPN

sp|Q5EXK1|3HBH_KLEOX

sp|Q949M8|3HID3_ARATH

sp|Q9CR21|ACPM_MOUSE

sp|P71864|3O1D1_MYCTU

sp|Q0TTH1|ANSME_CLOP1

sp|Q83R90|ABDH_SHIFL

sp|Q93VC3|ANS1_ORYSJ



sp|B0FWC6|NU2M_AEDAE

sp|O78680|NU2M_CARAU

sp|P0CD45|NU2C2_SOLBU

sp|Q534E0|NU2M_AILFU

sp|P0CC31|NU2C2_ANTAG

sp|Q9MTP3|NDHJ_OENEH

sp|B2J6S6|NDHK_NOSP7

sp|Q9S831|PSAE1_ARATH

sp|A4QJT7|NDHK_OLIPU

sp|Q9M3I7|NDHI_SPIOL

sp|Q9M3M1|NDHJ_SPIOL

sp|P09424|MTLD_ECOLI

sp|Q4L9Y4|MTLD_STAHJ

sp|B0Z5A8|PSBA_OENPA

sp|Q332Y2|PSBC_LACSA

sp|Q635P0|MTND_BACCZ

sp|Q7U4Z3|PSBA3_SYNPX

sp|Q68S10|PSBC_PANGI

sp|B2XWK1|PSBC_FAGEA

sp|Q1KVW6|PSBD_TETOB

sp|A6BM30|PSBC_GNEPA

sp|Q70Y08|PSBD_AMBTC

sp|Q0G9K2|PSBE_LIRTU

sp|Q2MIH1|PSBF_SOLBU

sp|Q67HB3|PSBF_ASPOF

sp|Q20EW2|PSBE_OLTVI

sp|Q731Q9|MTND_BACC1

sp|Q56317|PORB_THEMA

sp|Q49L03|PSBD_EUCGG

sp|B0JUK9|MTND_MICAN

sp|Q4VZH6|PSBF_CUCSA

sp|B1WQ89|PSBD_CROS5

sp|Q8CM25|PSBD_THEEB

sp|A4QJI3|PSBI_AETGR

sp|F9VEN7|QUEG_LACGL

sp|Q68RX8|PSBH_PANGI

sp|Q1XDD0|PSBD_PYRYE

sp|B2VAA3|MTND_SULSY

sp|Q85CN1|PSBI_ANTAG

sp|Q9KPA4|NADB_VIBCH

sp|B0Z4W7|PSBI_OENBI

sp|P12240|PSBI_THEVL

sp|Q31CN2|PSBJ_PROM9

sp|Q06GP6|PSBJ_PIPCE

sp|A7Y3F7|PSBJ_IPOPU

sp|Q8M

...


sp|Q8PXL6|DAPB_METMA

sp|Q11190|ETFD_CAEEL

sp|O46119|FRIH_ECHGR

sp|Q8K385|FRRS1_MOUSE

sp|B5FUI3|E4PD_SALDC

sp|A1RN69|E4PD_SHESW

sp|B5QXJ7|E4PD_SALEP

sp|Q8MIP0|FRIH_HORSE

sp|Q07103|FDH_NEUCR

sp|M1BYJ7|ENDB1_SOLTU

sp|Q7V7D4|DAPB_PROMM

sp|A0A0N0DCA3|DEP5_FUSLA

sp|B8B4W4|GLO19_ORYSI

sp|A8C7R6|EASC_CLAFS

sp|D5IGG6|FDR_SPHSX

sp|P00380|DYR_ENTFC

sp|Q5LLT7|DAPB_RUEPO

sp|Q2NER9|GGR3_METST

sp|D4AK47|EASE_ARTBC

sp|P19920|DCMM_OLICO

sp|A4Q8F7|GH109_ELIME

sp|Q6YT73|GLO5_ORYSJ

sp|A6LB54|GH109_PARD8

sp|Q9ZLI1|FTN_HELPJ

sp|A4FN60|GH109_SACEN

sp|S3D9F9|GLOC_GLAL2

sp|Q4WAW8|FTME_ASPFU

sp|E1WS50|FTN_BACF6

sp|Q8CNP5|FTN_STAES

sp|S0DQ98|FSR4_GIBF5

sp|Q8BGW1|FTO_MOUSE

sp|D4GYI2|GLPA1_HALVD

sp|Q65GY3|FENR1_BACLD

sp|Q1XDA1|FTRC_PYRYE

sp|Q5R7X0|FTO_PONAB

sp|A0R951|FENR1_BACAH

sp|Q8ETS1|FENR1_OCEIH

sp|A0LXL9|FENR1_GRAFK

sp|Q55389|FTRC_SYNY3

sp|A7GKN4|FENR1_BACCN

sp|B7MG07|GLPB_ECO45

sp|Q81XS0|FENR2_BACAN

sp|A8FYT6|DAPB_SHESH

sp|B5ET22|GLPB_ALIFM

sp|A8ADX8|GLPB_CITK8



sp|P77437|HYFF_ECOLI

sp|Q5WDH8|HISX_BACSK

sp|Q5LDB2|HCP_BACFN

sp|Q7M827|MFRA_WOLSU

sp|P0CI31|HCAB_ECOLI

sp|Q82W26|HISX_NITEU

sp|Q32DZ1|HCP_SHIDS

sp|B7JR48|HDOX_BACC0

sp|B4TRQ3|HCP_SALSV

sp|Q5L782|HEM1_CHLAB

sp|Q6AB02|HEM1_CUTAK

sp|A1K442|HEM1_AZOSB

sp|C3MJ24|HEM1_SULIL

sp|A0Q2B3|HEM1_CLONN

sp|Q9SLK0|ICDHX_ARATH

sp|A9WPH1|HEM1_RENSM

sp|Q4WR19|HELC_ASPFU

sp|A9L2D5|HEM1_SHEB9

sp|Q2KHZ4|MIA40_BOVIN

sp|A4HVU6|JBP2_LEIIN

sp|A3N0L8|MNMC_ACTP2

sp|B0BPE2|MNMC_ACTPJ

sp|A7H2B2|MNMC_CAMJD

sp|A2QK68|KTND_ASPNC

sp|A6VMR0|MNMC_ACTSZ

sp|Q62FV6|MNMC_BURMA

sp|Q6LNT9|MNMC_PHOPR

sp|Q8F0E4|MNMC_LEPIN

sp|Q8DB38|MNMC_VIBVU

sp|Q8ECR0|MNMC_SHEON

sp|A3M2P8|NUOA_ACIBT

sp|Q6G0J2|LLDD_BARQU

sp|B0V6L1|LLDD_ACIBY

sp|A3N3E5|LLDD_ACTP2

sp|B1IZI5|LLDD_ECOLC

sp|A5UFG9|LLDD_HAEIG

sp|B7L725|LLDD_ECO55

sp|C0Q1T7|LLDD_SALPC

sp|A4TKI4|LLDD_YERPP

sp|Q8FCB1|LLDD_ECOL6

sp|Q2R0L2|LAC19_ORYSJ

sp|Q62IN5|NUOA_BURMA

sp|Q03966|LAC1_CRYPA

sp|C3LWP7|LLDD_VIBCM

sp|Q12541|LAC1_AGABI

sp|B4T986|

sp|Q0DK35|GRXC7_ORYSJ

sp|P80873|GS39_BACSU

sp|A9R691|GPDA_YERPG

sp|P51110|DFRA_VITVI

sp|P80874|GS69_BACSU

sp|Q3MDZ9|GPDA_TRIV2

sp|P35571|GPDM_RAT

sp|Q9WWR3|CYOC_PSEPU

sp|O67716|DHAS_AQUAE

sp|P57523|DHAS_BUCAI

sp|O31440|CYPC_BACSU

sp|Q2NI00|DHQS_METST

sp|O76062|ERG24_HUMAN

sp|A0A0U2V7I8|CYP3_USTMD

sp|Q9LDR4|ERG24_ARATH

sp|P68434|ERG3_MYCBO

sp|P83695|DPS_BREBE

sp|P0C935|DPS_PORGI

sp|Q5PG12|DPS_SALPA

sp|Q6Y1R6|DPS_PROHU

sp|P43313|DPS_HELPY

sp|Q8XF78|DPS_SALTI

sp|A8XKG6|DPYD_CAEBR

sp|Q7XKU5|DAO_ORYSJ

sp|Q9C7S7|ERO1_ARATH

sp|P0AEA9|CYSG_ECO57

sp|B3GZA0|CYSG_ACTP7

sp|Q65T49|CYSG_MANSM

sp|B0BTC2|CYSG_ACTPJ

sp|A9MME5|CYSG_SALAR

sp|Q3KA85|CYSG_PSEPF

sp|Q15YU1|CYSG_PSEA6

sp|Q1QAX7|CYSG_PSYCK

sp|C6UCN7|CYSI_ECOBR

sp|P17846|CYSI_ECOLI

sp|A0BV78|DRE21_PARTE

sp|O32213|CYSI_BACSU

sp|B1MN34|CYSH_MYCA9

sp|B5QW35|CYSI_SALEP

sp|Q6FZ13|DAPB_BARQU

sp|Q4JK73|DHB11_MACFA

sp|P19574|DHF5_ERWCI

sp|Q9ZL20|DHOM_HELPJ

sp|P00372|DHML_METEA

sp|P00365|DHE2_NEUCR

sp|P28998|

sp|Q9LPC3|BBE1_ARATH

sp|Q944X7|AOP3V_ARATH

sp|P53109|AIM14_YEAST

sp|P84729|BAS1_PINST

sp|B5F7J0|ASTD_SALA4

sp|A5UUJ4|BCHL_ROSS1

sp|Q2ISY7|BCHB_RHOP2

sp|Q7ADE6|ASTD_ECO57

sp|Q7X2C7|BCHE_RUBGE

sp|A8H8E0|ASTD_SHEPA

sp|P26277|BCHZ_ROSDO

sp|B1XGK7|ASTD_ECODH

sp|Q81M95|ARGC_BACAN

sp|A9MAG5|ARGC_BRUC2

sp|B0RHD0|ARGC_CLAMS

sp|Q9A8H5|ARGC_CAUVC

sp|Q9RY72|ARGC_DEIRA

sp|C1DHY0|ARGC_AZOVD

sp|B8E0N8|ARGC_DICTD

sp|A0QHB4|ARGC_MYCA1

sp|O26934|ARGC_METTH

sp|P9WPZ9|ARGC_MYCTU

sp|A0B6F6|ARGC_METTP

sp|A4G1T4|ARGC_HERAR

sp|O87890|ARGC_NOSEL

sp|O87874|BCRC_THAAR

sp|B3E0U0|ARGC_METI4

sp|A0AJ40|ARGC_LISW6

sp|Q5ATH2|APDB_EMENI

sp|Q72RJ9|ARGC_LEPIC

sp|P44411|BCP_HAEIN

sp|Q9I5Q9|ARGC_PSEAE

sp|B1JE24|ARGC_PSEPW

sp|Q9VAI1|CIA30_DROME

sp|B8HGC3|ARGC_PSECP

sp|Q889Z3|ARGC_PSESM

sp|Q0MQ84|CIA30_PANTR

sp|C3K2Z7|ARGC_PSEFS

sp|Q1MIP7|ARGC_RHIL3

sp|Q9LQI7|CIA30_ARATH

sp|Q982X3|ARGC_RHILO

sp|A4FKC8|ARGC_SACEN

sp|A6UZG3|ARGC_PSEA7

sp|B5ZXZ1|ARGC_RHILW

sp|A5VXM5|ARGC_PSEP1

sp|A1Y

sp|V3TQ67|FRDA_SERS3

sp|P53573|ETFA_BRADU

sp|Q2KIG0|ETFD_BOVIN

sp|P0AEN2|FRE_ECOL6

sp|Q666Q0|E4PD_YERPS

sp|A7MJQ2|E4PD_CROS8

sp|A1A835|FRMA_ECOK1

sp|P06131|FDHA_METFO

sp|Q10CE4|GLO1_ORYSJ

sp|Q9FM82|GGLO4_ARATH

sp|Q2NFF7|GGR2_METST

sp|O27753|GGR2_METTH

sp|A8C7R7|EASD_CLAFS

sp|O57920|GGR_PYRHO

sp|P19917|DCMM_PSECH

sp|A9MR41|DAPB_SALAR

sp|P19915|DCMS_HYDPS

sp|Q9LJH5|GLO4_ARATH

sp|B5R1Q4|DAPB_SALEP

sp|B8B7C5|GLO5_ORYSI

sp|Q4WAX0|FTMG_ASPFU

sp|Q01772|GLOX_PHACH

sp|Q6G840|FTN_STAAS

sp|P0A999|FTNA_ECOL6

sp|B1KNF7|GH109_SHEWM

sp|S3E7Q2|GLOE_GLAL2

sp|Q01S58|GH109_SOLUE

sp|A9L0Q8|DAPB_SHEB9

sp|A3QGV8|DAPB_SHELP

sp|Q73EA6|FENR1_BACC1

sp|O31475|FENR1_BACSU

sp|P0A9C0|GLPA_ECOLI

sp|A8H756|DAPB_SHEPA

sp|B0BTN3|GLPB_ACTPJ

sp|P41344|FENR1_ORYSJ

sp|Q8D7Y4|GLPB_VIBVU

sp|B5YVQ3|GHRA_ECO5E

sp|A4W948|GHRA_ENT38

sp|A9C3H6|FENR_DELAS

sp|Q8Z7M6|GHRA_SALTI

sp|A5FJT9|FENR_FLAJ1

sp|A8AX95|DAPB_STRGC

sp|B1VXZ4|DAPB_STRGG

sp|B4SHT7|DAPB_STRM5

sp|B3WCB2|FENR_LACCB

sp|A4IS

## Create pandas dataframe using seqID & sequences

In [14]:
# create dataframe of 2000 additional isomerase sequences
#d_iso = {'name':seq_ids,'sequence':seqs}
d_1 = {'name':seqID,'sequence':t_seqs}
df = pd.DataFrame(d_1)
df.head()

name                                           sequence
0  sp|Q8L540|LTO1_ARATH  MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKC...
1  sp|Q9AL95|NROR_CLOAB  MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLN...
2    sp|P55931|ETFD_PIG  MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHY...
3  sp|Q16134|ETFD_HUMAN  MLVPLAKLSCLAYQCFHALKIKKNYLPLCATRWSSTSTVPRITTHY...
4  sp|Q9NZC7|WWOX_HUMAN  MAALRYAGLDDTDSEDELPPGWEERTTKDGWVYYANHTEEKTQWEH...

In [15]:
d_2 = {'name':seq_ids,'sequence':seqs}

df2 = pd.DataFrame(d_2)
df2.head()

name                                           sequence
0  sp|Q8L540|LTO1_ARATH  MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKC...
1  sp|Q9AL95|NROR_CLOAB  MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLN...
2    sp|P55931|ETFD_PIG  MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHY...
3  sp|Q16134|ETFD_HUMAN  MLVPLAKLSCLAYQCFHALKIKKNYLPLCATRWSSTSTVPRITTHY...
4  sp|Q9NZC7|WWOX_HUMAN  MAALRYAGLDDTDSEDELPPGWEERTTKDGWVYYANHTEEKTQWEH...

In [16]:
df.shape

(46750, 2)

In [17]:
df2.shape

(46750, 2)

In [18]:
# remove non-coding amino acid letters like X,B,U
df['sequence'] = df['sequence'].str.replace('U','G')
df['sequence'] = df['sequence'].str.replace('X','G')
df['sequence'] = df['sequence'].str.replace('B','G')

In [19]:
# remove non-coding amino acid letters like X,B,U
df2['sequence'] = df2['sequence'].str.replace('U','G')
df2['sequence'] = df2['sequence'].str.replace('X','G')
df2['sequence'] = df2['sequence'].str.replace('B','G')

In [20]:
#df['MW'] = df['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df.head()

In [21]:
#df2['MW'] = df2['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df2.head()

In [22]:
# Create 2 columns for the dataframe
df['classification'] = 'OXIDOREDUCTASE'
df['type'] = 5

df.head(10)

name                                           sequence  \
0   sp|Q8L540|LTO1_ARATH  MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKC...   
1   sp|Q9AL95|NROR_CLOAB  MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLN...   
2     sp|P55931|ETFD_PIG  MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHY...   
3   sp|Q16134|ETFD_HUMAN  MLVPLAKLSCLAYQCFHALKIKKNYLPLCATRWSSTSTVPRITTHY...   
4   sp|Q9NZC7|WWOX_HUMAN  MAALRYAGLDDTDSEDELPPGWEERTTKDGWVYYANHTEEKTQWEH...   
5  sp|Q9UHB4|NDOR1_HUMAN  MPSPQLLVLFGSQTGTAQDVSERLGREARRRRLGCRVQALDSYPVV...   
6  sp|Q6NPS8|NDOR1_ARATH  MGEKQRKLLVLYASQTGNALDAAERIGREAERRGLPASVVSTDEFD...   
7  sp|Q12181|NDOR1_YEAST  MSSSKKIVILYGSETGNAHDFATILSHRLHRWHFSHTFCSIGDYDP...   
8   sp|Q921G7|ETFD_MOUSE  MLVRLTKLSCPAYHWFHALKIKKCLPLCAPRCSSTSAVPQITTHYT...   
9   sp|P37769|KDUD_ECOLI  MILSAFSLEGKVAVVTGCDTGLGQGMALGLAQAGCDIVGINIVEPT...   

   classification  type  
0  OXIDOREDUCTASE     5  
1  OXIDOREDUCTASE     5  
2  OXIDOREDUCTASE     5  
3  OXIDOREDUCTASE     5  
4  OXIDOREDUCTASE     5  
5  OXIDOREDUCTASE     5  
6  OXIDOREDUCTASE     5  
7  OXIDOREDUCTASE     5  
8  OXIDOREDUCTASE     5  
9  OXIDOREDUCTASE     5

In [23]:
df.shape

(46750, 4)

In [24]:
# remove the duplicate protein sequences
df = df.drop_duplicates(subset='sequence', keep="first")
df.shape

(39793, 4)

In [25]:
df.head(10)

name                                           sequence  \
0   sp|Q8L540|LTO1_ARATH  MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKC...   
1   sp|Q9AL95|NROR_CLOAB  MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLN...   
2     sp|P55931|ETFD_PIG  MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHY...   
3   sp|Q16134|ETFD_HUMAN  MLVPLAKLSCLAYQCFHALKIKKNYLPLCATRWSSTSTVPRITTHY...   
4   sp|Q9NZC7|WWOX_HUMAN  MAALRYAGLDDTDSEDELPPGWEERTTKDGWVYYANHTEEKTQWEH...   
5  sp|Q9UHB4|NDOR1_HUMAN  MPSPQLLVLFGSQTGTAQDVSERLGREARRRRLGCRVQALDSYPVV...   
6  sp|Q6NPS8|NDOR1_ARATH  MGEKQRKLLVLYASQTGNALDAAERIGREAERRGLPASVVSTDEFD...   
7  sp|Q12181|NDOR1_YEAST  MSSSKKIVILYGSETGNAHDFATILSHRLHRWHFSHTFCSIGDYDP...   
8   sp|Q921G7|ETFD_MOUSE  MLVRLTKLSCPAYHWFHALKIKKCLPLCAPRCSSTSAVPQITTHYT...   
9   sp|P37769|KDUD_ECOLI  MILSAFSLEGKVAVVTGCDTGLGQGMALGLAQAGCDIVGINIVEPT...   

   classification  type  
0  OXIDOREDUCTASE     5  
1  OXIDOREDUCTASE     5  
2  OXIDOREDUCTASE     5  
3  OXIDOREDUCTASE     5  
4  OXIDOREDUCTASE     5  
5  OXIDOREDUCTASE     5  
6  OXIDOREDUCTASE     5  
7  OXIDOREDUCTASE     5  
8  OXIDOREDUCTASE     5  
9  OXIDOREDUCTASE     5

## Save dataframe of sequences as a csv file

In [27]:
df.to_csv('uniprot-oxidoreductase-Feb1.csv',index = None)

proteins = pd.read_csv('uniprot-oxidoreductase-Feb1.csv')

proteins.head()

name                                           sequence  \
0  sp|Q8L540|LTO1_ARATH  MMARFVSVSSCQFHFGFREVSPPSVTSYPRRFEVSDRRFPAIPIKC...   
1  sp|Q9AL95|NROR_CLOAB  MKSTKILILGAGPAGFSAAKAALGKCDDITMINSEKYLPYYRPRLN...   
2    sp|P55931|ETFD_PIG  MMVPLAKLASPAYQCFHALKIKKNYLPLCATRWSSTCKVPRITTHY...   
3  sp|Q16134|ETFD_HUMAN  MLVPLAKLSCLAYQCFHALKIKKNYLPLCATRWSSTSTVPRITTHY...   
4  sp|Q9NZC7|WWOX_HUMAN  MAALRYAGLDDTDSEDELPPGWEERTTKDGWVYYANHTEEKTQWEH...   

   classification  type  
0  OXIDOREDUCTASE     5  
1  OXIDOREDUCTASE     5  
2  OXIDOREDUCTASE     5  
3  OXIDOREDUCTASE     5  
4  OXIDOREDUCTASE     5

In [28]:
proteins.shape

(39793, 4)